In [1]:
import os
import tensorflow as tf
import pandas as pd
import numpy as np
import plotly.graph_objs as go
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import cross_val_score, train_test_split
from sklearn.preprocessing import OrdinalEncoder
from sklearn import metrics
from sklearn.metrics import confusion_matrix, accuracy_score
import hdbscan

/home/skyolia/anaconda3/envs/tensorflow_gpuenv/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:523: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/skyolia/anaconda3/envs/tensorflow_gpuenv/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:524: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/skyolia/anaconda3/envs/tensorflow_gpuenv/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:525: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/home/skyo

In [36]:
#https://towardsdatascience.com/segmenting-credit-card-customers-with-machine-learning-ed4dbcea009c
x = pd.read_csv('/home/skyolia/JupyterProjects/data/credit_card/CC GENERAL.csv', sep=',')
x

CUST_ID      BALANCE  BALANCE_FREQUENCY  PURCHASES  ONEOFF_PURCHASES  \
0     C10001    40.900749           0.818182      95.40              0.00   
1     C10002  3202.467416           0.909091       0.00              0.00   
2     C10003  2495.148862           1.000000     773.17            773.17   
3     C10004  1666.670542           0.636364    1499.00           1499.00   
4     C10005   817.714335           1.000000      16.00             16.00   
...      ...          ...                ...        ...               ...   
8945  C19186    28.493517           1.000000     291.12              0.00   
8946  C19187    19.183215           1.000000     300.00              0.00   
8947  C19188    23.398673           0.833333     144.40              0.00   
8948  C19189    13.457564           0.833333       0.00              0.00   
8949  C19190   372.708075           0.666667    1093.25           1093.25   

      INSTALLMENTS_PURCHASES  CASH_ADVANCE  PURCHASES_FREQUENCY  \
0                      95.40      0.000000             0.166667   
1                       0.00   6442.945483             0.000000   
2                       0.00      0.000000             1.000000   
3                       0.00    205.788017             0.083333   
4                       0.00      0.000000             0.083333   
...                      ...           ...                  ...   
8945                  291.12      0.000000             1.000000   
8946                  300.00      0.000000             1.000000   
8947                  144.40      0.000000             0.833333   
8948                    0.00     36.558778             0.000000   
8949                    0.00    127.040008             0.666667   

      ONEOFF_PURCHASES_FREQUENCY  PURCHASES_INSTALLMENTS_FREQUENCY  \
0                       0.000000                          0.083333   
1                       0.000000                          0.000000   
2                       1.000000                          0.000000   
3                       0.083333                          0.000000   
4                       0.083333                          0.000000   
...                          ...                               ...   
8945                    0.000000                          0.833333   
8946                    0.000000                          0.833333   
8947                    0.000000                          0.666667   
8948                    0.000000                          0.000000   
8949                    0.666667                          0.000000   

      CASH_ADVANCE_FREQUENCY  CASH_ADVANCE_TRX  PURCHASES_TRX  CREDIT_LIMIT  \
0                   0.000000                 0              2        1000.0   
1                   0.250000                 4              0        7000.0   
2                   0.000000                 0             12        7500.0   
3                   0.083333                 1              1        7500.0   
4                   0.000000                 0              1        1200.0   
...                      ...               ...            ...           ...   
8945                0.000000                 0              6        1000.0   
8946                0.000000                 0              6        1000.0   
8947                0.000000                 0              5        1000.0   
8948                0.166667                 2              0         500.0   
8949                0.333333                 2             23        1200.0   

         PAYMENTS  MINIMUM_PAYMENTS  PRC_FULL_PAYMENT  TENURE  
0      201.802084        139.509787          0.000000      12  
1     4103.032597       1072.340217          0.222222      12  
2      622.066742        627.284787          0.000000      12  
3        0.000000               NaN          0.000000      12  
4      678.334763        244.791237          0.000000      12  
...           ...               ...               ...     ...  
8945   325.594462         48.886365  

In [37]:
x['MINIMUM_PAYMENTS'].fillna((x['MINIMUM_PAYMENTS'].median()), inplace=True)
x['CREDIT_LIMIT'].fillna((x['CREDIT_LIMIT'].median()), inplace=True)
ids = x['CUST_ID']
x.drop(columns=['CUST_ID'], inplace=True)
x

BALANCE  BALANCE_FREQUENCY  PURCHASES  ONEOFF_PURCHASES  \
0       40.900749           0.818182      95.40              0.00   
1     3202.467416           0.909091       0.00              0.00   
2     2495.148862           1.000000     773.17            773.17   
3     1666.670542           0.636364    1499.00           1499.00   
4      817.714335           1.000000      16.00             16.00   
...           ...                ...        ...               ...   
8945    28.493517           1.000000     291.12              0.00   
8946    19.183215           1.000000     300.00              0.00   
8947    23.398673           0.833333     144.40              0.00   
8948    13.457564           0.833333       0.00              0.00   
8949   372.708075           0.666667    1093.25           1093.25   

      INSTALLMENTS_PURCHASES  CASH_ADVANCE  PURCHASES_FREQUENCY  \
0                      95.40      0.000000             0.166667   
1                       0.00   6442.945483             0.000000   
2                       0.00      0.000000             1.000000   
3                       0.00    205.788017             0.083333   
4                       0.00      0.000000             0.083333   
...                      ...           ...                  ...   
8945                  291.12      0.000000             1.000000   
8946                  300.00      0.000000             1.000000   
8947                  144.40      0.000000             0.833333   
8948                    0.00     36.558778             0.000000   
8949                    0.00    127.040008             0.666667   

      ONEOFF_PURCHASES_FREQUENCY  PURCHASES_INSTALLMENTS_FREQUENCY  \
0                       0.000000                          0.083333   
1                       0.000000                          0.000000   
2                       1.000000                          0.000000   
3                       0.083333                          0.000000   
4                       0.083333                          0.000000   
...                          ...                               ...   
8945                    0.000000                          0.833333   
8946                    0.000000                          0.833333   
8947                    0.000000                          0.666667   
8948                    0.000000                          0.000000   
8949                    0.666667                          0.000000   

      CASH_ADVANCE_FREQUENCY  CASH_ADVANCE_TRX  PURCHASES_TRX  CREDIT_LIMIT  \
0                   0.000000                 0              2        1000.0   
1                   0.250000                 4              0        7000.0   
2                   0.000000                 0             12        7500.0   
3                   0.083333                 1              1        7500.0   
4                   0.000000                 0              1        1200.0   
...                      ...               ...            ...           ...   
8945                0.000000                 0              6        1000.0   
8946                0.000000                 0              6        1000.0   
8947                0.000000                 0              5        1000.0   
8948                0.166667                 2              0         500.0   
8949                0.333333                 2             23        1200.0   

         PAYMENTS  MINIMUM_PAYMENTS  PRC_FULL_PAYMENT  TENURE  
0      201.802084        139.509787          0.000000      12  
1     4103.032597       1072.340217          0.222222      12  
2      622.066742        627.284787          0.000000      12  
3        0.000000        312.343947          0.000000      12  
4      678.334763        244.791237          0.000000      12  
...           ...               ...               ...     ...  
8945   325.594462         48.886365          0.500000       6  
8946   275.861322        312.343947          0.000000       6  
8947    81

In [38]:
x.isna().sum()

BALANCE                             0
BALANCE_FREQUENCY                   0
PURCHASES                           0
ONEOFF_PURCHASES                    0
INSTALLMENTS_PURCHASES              0
CASH_ADVANCE                        0
PURCHASES_FREQUENCY                 0
ONEOFF_PURCHASES_FREQUENCY          0
PURCHASES_INSTALLMENTS_FREQUENCY    0
CASH_ADVANCE_FREQUENCY              0
CASH_ADVANCE_TRX                    0
PURCHASES_TRX                       0
CREDIT_LIMIT                        0
PAYMENTS                            0
MINIMUM_PAYMENTS                    0
PRC_FULL_PAYMENT                    0
TENURE                              0
dtype: int64

In [6]:
fig = go.Figure(data=go.Heatmap(z=x.corr(), x=x.columns, y=x.columns))
fig.show()

In [39]:
scaler = MinMaxScaler(feature_range=(0, 1))
cols = x.columns
x = scaler.fit_transform(x)
x = pd.DataFrame(data=x, columns=cols)
train, test = train_test_split(x, test_size = 0.2, random_state = 0)
train

BALANCE  BALANCE_FREQUENCY  PURCHASES  ONEOFF_PURCHASES  \
2070  0.260229           1.000000   0.000000          0.000000   
3485  0.034198           1.000000   0.034597          0.034965   
2124  0.131722           1.000000   0.017844          0.012509   
3021  0.005908           0.600000   0.009370          0.006738   
6342  0.126853           1.000000   0.002558          0.000000   
...        ...                ...        ...               ...   
4373  0.001594           1.000000   0.006963          0.000000   
7891  0.070052           1.000000   0.000000          0.000000   
4859  0.001636           0.545455   0.006118          0.000000   
3264  0.450100           1.000000   0.000000          0.000000   
2732  0.013609           1.000000   0.040210          0.038786   

      INSTALLMENTS_PURCHASES  CASH_ADVANCE  PURCHASES_FREQUENCY  \
2070                0.000000      0.073859             0.000000   
3485                0.012062      0.000000             1.000000   
2124                0.016229      0.000000             1.000000   
3021                0.008216      0.000000             0.500000   
6342                0.005576      0.000000             0.583333   
...                      ...           ...                  ...   
4373                0.015177      0.000000             1.000000   
7891                0.000000      0.003232             0.000000   
4859                0.013333      0.000000             0.500000   
3264                0.000000      0.138825             0.000000   
2732                0.017374      0.000411             0.833333   

      ONEOFF_PURCHASES_FREQUENCY  PURCHASES_INSTALLMENTS_FREQUENCY  \
2070                         0.0                          0.000000   
3485                         1.0                          0.333333   
2124                         0.5                          1.000000   
3021                         0.2                          0.300000   
6342                         0.0                          0.583333   
...                          ...                               ...   
4373                         0.0                          1.000000   
7891                         0.0                          0.000000   
4859                         0.0                          0.500000   
3264                         0.0                          0.000000   
2732                         0.5                          0.500000   

      CASH_ADVANCE_FREQUENCY  CASH_ADVANCE_TRX  PURCHASES_TRX  CREDIT_LIMIT  \
2070                0.611111          0.211382       0.000000      0.215359   
3485                0.000000          0.000000       0.100559      0.151920   
2124                0.000000          0.000000       0.081006      0.085142   
3021                0.000000          0.000000       0.036313      0.038397   
6342                0.000000          0.000000       0.019553      0.098497   
...                      ...               ...            ...           ...   
4373                0.000000          0.000000       0.041899      0.131886   
7891                0.055555          0.008130       0.000000      0.048414   
4859                0.000000          0.000000       0.016760      0.382304   
3264                0.333333          0.121951       0.000000      0.332220   
2732                0.055555          0.008130       0.055866      0.058431   

      PAYMENTS  MINIMUM_PAYMENTS  PRC_FULL_PAYMENT    TENURE  
2070  0.024699          0.020578          0.000000  1.000000  
3485  0.033072          0.002905          0.000000  1.000000  
2124  0.024863          0.015825          0.000000  1.000000  
3021  0.004172          0.001352          0.000000  0.666667  
6342  0.012221          0.008221          0.000000  1.000000  
...        ...               ...               ...       ...  
4373  0.007516          0.002340          0.916667  1.000000  
7891  0.006152          0.003608          0.000000  1.000000  
4859  0.012207          0.002122          1.000000  

In [40]:
class MySequence(tf.keras.utils.Sequence):

    def __init__(self, x, y, batch_size):
        self.x, self.y = x, y
        self.batch_size = batch_size

    def __len__(self):
        return int(np.ceil(len(self.x) / float(self.batch_size)))

    def __getitem__(self, idx):
        batch_x = self.x[idx * self.batch_size:(idx + 1) * self.batch_size]
        batch_y = self.y[idx * self.batch_size:(idx + 1) * self.batch_size]
        return batch_x, batch_y
    
class Sampling(tf.keras.layers.Layer):
    """Uses (z_mean, z_log_var) to sample z, the vector encoding a digit."""

    def call(self, inputs):
        z_mean, z_log_var = inputs
        batch = tf.shape(z_mean)[0]
        dim = tf.shape(z_mean)[1]
        epsilon = tf.keras.backend.random_normal(shape=(batch, dim))
        return z_mean + tf.exp(0.5 * z_log_var) * epsilon
    
class VAE:
    def __init__(self, in_shape, latent_dim, units=None, factors=None, dropout=None, **kwargs):
        super(VAE, self).__init__(**kwargs)
        self.in_shape = in_shape
        self.latent_dim = latent_dim
        self.units = units
        self.factors = factors
        self.dropout = dropout
    
    def __build_block__(self, input_layer, units, activation='elu', dropout=0, norm=True):
        layer = tf.keras.layers.Dense(units, use_bias=not norm, kernel_initializer='glorot_normal')(input_layer)
        if norm:
            layer = tf.keras.layers.BatchNormalization()(layer)
        layer = tf.keras.layers.Activation(activation)(layer)
        layer = tf.keras.layers.Dropout(dropout)(layer)
        return layer
    
    def __build_encoder__(self, layer):
        if self.factors:
            self.factors.insert(0, self.in_shape)
            self.units = np.cumprod(self.factors).tolist()[1:]
        if self.units:
            self.dropout = np.zeros_like(self.units).tolist() if self.dropout is None else self.dropout
            for i, j in zip(self.units, self.dropout):
                layer = self.__build_block__(layer, i, dropout=j)
        return layer
    
    def __build_latent__(self, layer):
        z_mean = tf.keras.layers.Dense(self.latent_dim, name="z_mean")(layer)
        z_log_var = tf.keras.layers.Dense(self.latent_dim, name="z_log_var")(layer)
        z = Sampling()([z_mean, z_log_var])
        return z, z_mean, z_log_var
    
    def __build_decoder__(self, layer):
        if self.units:
            self.units.reverse(), self.dropout.reverse()
            for i in self.units:
                layer = self.__build_block__(layer, i)
        layer = self.__build_block__(layer, self.in_shape, activation='linear', norm=False)
        return layer
    
    def __call__(self):
        inputs = tf.keras.layers.Input(shape=(self.in_shape, ), name='encoder_input_layer')
        encoder = self.__build_encoder__(inputs)
        z, z_mean, z_log_var = self.__build_latent__(encoder)
        decoder = self.__build_decoder__(z)
        latent = tf.keras.Model(inputs=inputs, outputs=[z, z_mean, z_log_var], name="encoder")
        model = tf.keras.Model(inputs=inputs, outputs=decoder, name="decoder")
        return z_mean, z_log_var, latent, model
        

hp = [ 0.82842651,  0.18310614,  0.62111806,  0.52785986,  0.10190886,  0.24344705,
 18.04326615,  0.82996059]
z_mean, z_log_var, latent, model = VAE(train.shape[1], latent_dim=2, units=[16, 14, 12, 10, 8, 6, 4])()
latent.summary()

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
encoder_input_layer (InputLayer (None, 17)           0                                            
__________________________________________________________________________________________________
dense_75 (Dense)                (None, 16)           272         encoder_input_layer[0][0]        
__________________________________________________________________________________________________
batch_normalization_70 (BatchNo (None, 16)           64          dense_75[0][0]                   
__________________________________________________________________________________________________
activation_75 (Activation)      (None, 16)           0           batch_normalization_70[0][0]     
__________________________________________________________________________________________________
dropout_75

In [19]:
#https://towardsdatascience.com/variational-autoencoders-vaes-for-dummies-step-by-step-tutorial-69e6d1c9d8e9
#https://medium.com/red-buffer/autoencoders-guide-and-code-in-tensorflow-2-0-a4101571ce56
#https://keras.io/examples/generative/vae/

def vae_loss(x, x_bar):
    return tf.losses.mean_squared_error(x, x_bar) - (0.5 * tf.reduce_sum(1 + z_log_var - tf.math.pow(z_mean, 2) - tf.exp(z_log_var)))


epochs, batch_size, lr, filepath = 5000, 256, 1e-2, "test.weights.best.hdf5"
steps_per_epoch = int(np.ceil(train.shape[0]/batch_size))

train_generator = MySequence(train, train, batch_size)
test_generator = MySequence(test, test, batch_size)
checkpoint = tf.keras.callbacks.ModelCheckpoint(filepath, monitor='val_loss', verbose=1, save_best_only=True)
tb = tf.keras.callbacks.TensorBoard(log_dir=os.getcwd())

opt = tf.keras.optimizers.Adam() #
model.compile(loss=vae_loss, optimizer=opt)
model.fit_generator(train_generator,
                    steps_per_epoch=steps_per_epoch,
                    epochs=epochs,
                    verbose=1,
                    validation_data=test_generator,
                    validation_steps=int(np.ceil(test.shape[0]/batch_size)),
                    use_multiprocessing=False,
                    workers=12,
                    shuffle=True,
                    #initial_epoch=65,
                    callbacks=[checkpoint, tb])

Epoch 1/5000
27/28 [===========================>..] - ETA: 0s - loss: 166.8910
Epoch 00001: val_loss improved from inf to 17.12281, saving model to test.weights.best.hdf5
28/28 [==============================] - 6s 229ms/step - loss: 164.5916 - val_loss: 17.1228
Epoch 2/5000
26/28 [==========================>...] - ETA: 0s - loss: 74.2236
Epoch 00002: val_loss improved from 17.12281 to 9.83276, saving model to test.weights.best.hdf5
28/28 [==============================] - 1s 23ms/step - loss: 72.2673 - val_loss: 9.8328
Epoch 3/5000
25/28 [=========================>....] - ETA: 0s - loss: 41.1978
Epoch 00003: val_loss did not improve from 9.83276
28/28 [==============================] - 0s 17ms/step - loss: 40.5455 - val_loss: 13.1004
Epoch 4/5000
24/28 [========================>.....] - ETA: 0s - loss: 28.6325
Epoch 00004: val_loss did not improve from 9.83276
28/28 [==============================] - 1s 19ms/step - loss: 28.1005 - val_loss: 19.0017
Epoch 5/5000
25/28 [================

28/28 [==============================] - 1s 24ms/step - loss: 0.3149 - val_loss: 0.3565
Epoch 34/5000
25/28 [=========================>....] - ETA: 0s - loss: 0.2988
Epoch 00034: val_loss improved from 0.35654 to 0.33359, saving model to test.weights.best.hdf5
28/28 [==============================] - 1s 21ms/step - loss: 0.2980 - val_loss: 0.3336
Epoch 35/5000
25/28 [=========================>....] - ETA: 0s - loss: 0.2832
Epoch 00035: val_loss improved from 0.33359 to 0.30664, saving model to test.weights.best.hdf5
28/28 [==============================] - 1s 22ms/step - loss: 0.2825 - val_loss: 0.3066
Epoch 36/5000
25/28 [=========================>....] - ETA: 0s - loss: 0.2671
Epoch 00036: val_loss improved from 0.30664 to 0.28841, saving model to test.weights.best.hdf5
28/28 [==============================] - 1s 21ms/step - loss: 0.2680 - val_loss: 0.2884
Epoch 37/5000
25/28 [=========================>....] - ETA: 0s - loss: 0.2560
Epoch 00037: val_loss improved from 0.28841 to 0.27

24/28 [========================>.....] - ETA: 0s - loss: 0.1058
Epoch 00065: val_loss improved from 0.09911 to 0.09740, saving model to test.weights.best.hdf5
28/28 [==============================] - 1s 22ms/step - loss: 0.1056 - val_loss: 0.0974
Epoch 66/5000
24/28 [========================>.....] - ETA: 0s - loss: 0.1029
Epoch 00066: val_loss improved from 0.09740 to 0.09509, saving model to test.weights.best.hdf5
28/28 [==============================] - 1s 22ms/step - loss: 0.1033 - val_loss: 0.0951
Epoch 67/5000
27/28 [===========================>..] - ETA: 0s - loss: 0.1013
Epoch 00067: val_loss improved from 0.09509 to 0.09274, saving model to test.weights.best.hdf5
28/28 [==============================] - 1s 20ms/step - loss: 0.1014 - val_loss: 0.0927
Epoch 68/5000
27/28 [===========================>..] - ETA: 0s - loss: 0.1004
Epoch 00068: val_loss improved from 0.09274 to 0.09151, saving model to test.weights.best.hdf5
28/28 [==============================] - 1s 20ms/step - lo

Epoch 97/5000
24/28 [========================>.....] - ETA: 0s - loss: 0.0725
Epoch 00097: val_loss improved from 0.06555 to 0.06499, saving model to test.weights.best.hdf5
28/28 [==============================] - 1s 20ms/step - loss: 0.0729 - val_loss: 0.0650
Epoch 98/5000
26/28 [==========================>...] - ETA: 0s - loss: 0.0728
Epoch 00098: val_loss improved from 0.06499 to 0.06481, saving model to test.weights.best.hdf5
28/28 [==============================] - 1s 21ms/step - loss: 0.0725 - val_loss: 0.0648
Epoch 99/5000
26/28 [==========================>...] - ETA: 0s - loss: 0.0726
Epoch 00099: val_loss improved from 0.06481 to 0.06414, saving model to test.weights.best.hdf5
28/28 [==============================] - 1s 21ms/step - loss: 0.0717 - val_loss: 0.0641
Epoch 100/5000
25/28 [=========================>....] - ETA: 0s - loss: 0.0708
Epoch 00100: val_loss did not improve from 0.06414
28/28 [==============================] - 0s 18ms/step - loss: 0.0716 - val_loss: 0.0643

27/28 [===========================>..] - ETA: 0s - loss: 0.0606
Epoch 00130: val_loss improved from 0.05446 to 0.05390, saving model to test.weights.best.hdf5
28/28 [==============================] - 1s 21ms/step - loss: 0.0607 - val_loss: 0.0539
Epoch 131/5000
25/28 [=========================>....] - ETA: 0s - loss: 0.0602
Epoch 00131: val_loss improved from 0.05390 to 0.05347, saving model to test.weights.best.hdf5
28/28 [==============================] - 1s 21ms/step - loss: 0.0604 - val_loss: 0.0535
Epoch 132/5000
25/28 [=========================>....] - ETA: 0s - loss: 0.0594
Epoch 00132: val_loss improved from 0.05347 to 0.05315, saving model to test.weights.best.hdf5
28/28 [==============================] - 1s 22ms/step - loss: 0.0596 - val_loss: 0.0532
Epoch 133/5000
25/28 [=========================>....] - ETA: 0s - loss: 0.0616
Epoch 00133: val_loss improved from 0.05315 to 0.05299, saving model to test.weights.best.hdf5
28/28 [==============================] - 1s 21ms/step -

...

Epoch 830/5000
25/28 [=========================>....] - ETA: 0s - loss: 0.0391
Epoch 00830: val_loss did not improve from 0.03912
28/28 [==============================] - 0s 17ms/step - loss: 0.0391 - val_loss: 0.0392
Epoch 831/5000
25/28 [=========================>....] - ETA: 0s - loss: 0.0391
Epoch 00831: val_loss did not improve from 0.03912
28/28 [==============================] - 0s 17ms/step - loss: 0.0391 - val_loss: 0.0392
Epoch 832/5000
25/28 [=========================>....] - ETA: 0s - loss: 0.0391
Epoch 00832: val_loss did not improve from 0.03912
28/28 [==============================] - 0s 17ms/step - loss: 0.0391 - val_loss: 0.0394
Epoch 833/5000
25/28 [=========================>....] - ETA: 0s - loss: 0.0392
Epoch 00833: val_loss did not improve from 0.03912
28/28 [==============================] - 0s 17ms/step - loss: 0.0391 - val_loss: 0.0392
Epoch 834/5000
25/28 [=========================>....] - ETA: 0s - loss: 0.0392
Epoch 00834: val_loss did not improve from 0.0391

Epoch 868/5000
26/28 [==========================>...] - ETA: 0s - loss: 0.0391
Epoch 00868: val_loss did not improve from 0.03912
28/28 [==============================] - 0s 17ms/step - loss: 0.0391 - val_loss: 0.0393
Epoch 869/5000
26/28 [==========================>...] - ETA: 0s - loss: 0.0393
Epoch 00869: val_loss did not improve from 0.03912
28/28 [==============================] - 0s 18ms/step - loss: 0.0391 - val_loss: 0.0393
Epoch 870/5000
24/28 [========================>.....] - ETA: 0s - loss: 0.0390
Epoch 00870: val_loss did not improve from 0.03912
28/28 [==============================] - 0s 17ms/step - loss: 0.0391 - val_loss: 0.0392
Epoch 871/5000
25/28 [=========================>....] - ETA: 0s - loss: 0.0392
Epoch 00871: val_loss did not improve from 0.03912
28/28 [==============================] - 0s 17ms/step - loss: 0.0391 - val_loss: 0.0393
Epoch 872/5000
25/28 [=========================>....] - ETA: 0s - loss: 0.0391
Epoch 00872: val_loss did not improve from 0.0391

Epoch 906/5000
26/28 [==========================>...] - ETA: 0s - loss: 0.0392
Epoch 00906: val_loss did not improve from 0.03912
28/28 [==============================] - 0s 17ms/step - loss: 0.0391 - val_loss: 0.0393
Epoch 907/5000
26/28 [==========================>...] - ETA: 0s - loss: 0.0392
Epoch 00907: val_loss did not improve from 0.03912
28/28 [==============================] - 0s 17ms/step - loss: 0.0391 - val_loss: 0.0392
Epoch 908/5000
25/28 [=========================>....] - ETA: 0s - loss: 0.0389
Epoch 00908: val_loss did not improve from 0.03912
28/28 [==============================] - 0s 17ms/step - loss: 0.0391 - val_loss: 0.0392
Epoch 909/5000
26/28 [==========================>...] - ETA: 0s - loss: 0.0392
Epoch 00909: val_loss did not improve from 0.03912
28/28 [==============================] - 0s 17ms/step - loss: 0.0391 - val_loss: 0.0392
Epoch 910/5000
26/28 [==========================>...] - ETA: 0s - loss: 0.0392
Epoch 00910: val_loss did not improve from 0.0391

Epoch 944/5000
25/28 [=========================>....] - ETA: 0s - loss: 0.0393
Epoch 00944: val_loss did not improve from 0.03912
28/28 [==============================] - 0s 17ms/step - loss: 0.0393 - val_loss: 0.0395
Epoch 945/5000
25/28 [=========================>....] - ETA: 0s - loss: 0.0391
Epoch 00945: val_loss did not improve from 0.03912
28/28 [==============================] - 0s 17ms/step - loss: 0.0391 - val_loss: 0.0395
Epoch 946/5000
26/28 [==========================>...] - ETA: 0s - loss: 0.0390
Epoch 00946: val_loss did not improve from 0.03912
28/28 [==============================] - 0s 17ms/step - loss: 0.0391 - val_loss: 0.0393
Epoch 947/5000
25/28 [=========================>....] - ETA: 0s - loss: 0.0393
Epoch 00947: val_loss did not improve from 0.03912
28/28 [==============================] - 0s 17ms/step - loss: 0.0391 - val_loss: 0.0392
Epoch 948/5000
25/28 [=========================>....] - ETA: 0s - loss: 0.0390
Epoch 00948: val_loss did not improve from 0.0391

KeyboardInterrupt: 

In [41]:
epochs, batch_size, lr, filepath = 5000, 256, 1e-2, "test.weights.best.hdf5"
steps_per_epoch = int(np.ceil(train.shape[0]/batch_size))

train_generator = MySequence(train, train, batch_size)
test_generator = MySequence(test, test, batch_size)

model.load_weights(filepath)
opt = tf.keras.optimizers.Adam() # 
model.compile(loss=vae_loss, optimizer=opt)
scores = model.evaluate(test_generator, batch_size=batch_size)
scores

7/7 [==============================] - 1s 177ms/step


0.03912414489261931

In [27]:
_, z_mean, z_var = latent.predict(x.values[[0]])
z_mean[0,0]

0.00014600717

In [29]:
import plotly.figure_factory as ff

_, z_mean, z_var = latent.predict(x.values[[0]])
x = np.random.normal(z_mean[0,0], np.exp(z_var[0,0]), 1000)
hist_data = [x]
group_labels = ['distplot'] # name of the dataset

fig = ff.create_distplot(hist_data, group_labels)
fig.show()

In [42]:
z, _, _ = latent.predict(x.values)
fig = go.Figure(data=go.Scatter(x=z[:,0], y=z[:,1], mode='markers'))
fig.show()

In [46]:
new = model.predict(x.values[[0]])
new

array([[0.07778844, 0.8991155 , 0.01815174, 0.00744253, 0.01106814,
        0.02476274, 0.5014203 , 0.20460245, 0.37171906, 0.08220331,
        0.02602808, 0.03946033, 0.14094731, 0.02765048, 0.01107735,
        0.1463655 , 0.9311384 ]], dtype=float32)

In [47]:
x.values[0]

array([0.00214779, 0.818182  , 0.00194537, 0.        , 0.00424   ,
       0.        , 0.166667  , 0.        , 0.083333  , 0.        ,
       0.        , 0.00558659, 0.03171953, 0.00397863, 0.00182565,
       0.        , 1.        ])

In [35]:
fig = go.Figure()
for i in np.unique(cluster_labels):
    idx = np.where(cluster_labels==i)[0]
    fig.add_trace(go.Scatter(x=umap[idx,0], y=umap[idx,1], mode='markers', name='cluster_'+str(i)))
fig.show()

In [93]:
df = pd.read_csv('/home/skyolia/JupyterProjects/data/credit_card/CC GENERAL.csv', sep=',')
df['MINIMUM_PAYMENTS'].fillna((df['MINIMUM_PAYMENTS'].median()), inplace=True)
df['CREDIT_LIMIT'].fillna((df['CREDIT_LIMIT'].median()), inplace=True)
df['Clusters'] = cluster_labels
df.to_csv('/home/skyolia/JupyterProjects/data/credit_card/clustered_data.csv', index=False, sep=',')

In [2]:
df = pd.read_csv('/home/skyolia/JupyterProjects/data/credit_card/clustered_data.csv', sep=',')
df

CUST_ID      BALANCE  BALANCE_FREQUENCY  PURCHASES  ONEOFF_PURCHASES  \
0     C10001    40.900749           0.818182      95.40              0.00   
1     C10002  3202.467416           0.909091       0.00              0.00   
2     C10003  2495.148862           1.000000     773.17            773.17   
3     C10004  1666.670542           0.636364    1499.00           1499.00   
4     C10005   817.714335           1.000000      16.00             16.00   
...      ...          ...                ...        ...               ...   
8945  C19186    28.493517           1.000000     291.12              0.00   
8946  C19187    19.183215           1.000000     300.00              0.00   
8947  C19188    23.398673           0.833333     144.40              0.00   
8948  C19189    13.457564           0.833333       0.00              0.00   
8949  C19190   372.708075           0.666667    1093.25           1093.25   

      INSTALLMENTS_PURCHASES  CASH_ADVANCE  PURCHASES_FREQUENCY  \
0                      95.40      0.000000             0.166667   
1                       0.00   6442.945483             0.000000   
2                       0.00      0.000000             1.000000   
3                       0.00    205.788017             0.083333   
4                       0.00      0.000000             0.083333   
...                      ...           ...                  ...   
8945                  291.12      0.000000             1.000000   
8946                  300.00      0.000000             1.000000   
8947                  144.40      0.000000             0.833333   
8948                    0.00     36.558778             0.000000   
8949                    0.00    127.040008             0.666667   

      ONEOFF_PURCHASES_FREQUENCY  PURCHASES_INSTALLMENTS_FREQUENCY  \
0                       0.000000                          0.083333   
1                       0.000000                          0.000000   
2                       1.000000                          0.000000   
3                       0.083333                          0.000000   
4                       0.083333                          0.000000   
...                          ...                               ...   
8945                    0.000000                          0.833333   
8946                    0.000000                          0.833333   
8947                    0.000000                          0.666667   
8948                    0.000000                          0.000000   
8949                    0.666667                          0.000000   

      CASH_ADVANCE_FREQUENCY  CASH_ADVANCE_TRX  PURCHASES_TRX  CREDIT_LIMIT  \
0                   0.000000                 0              2        1000.0   
1                   0.250000                 4              0        7000.0   
2                   0.000000                 0             12        7500.0   
3                   0.083333                 1              1        7500.0   
4                   0.000000                 0              1        1200.0   
...                      ...               ...            ...           ...   
8945                0.000000                 0              6        1000.0   
8946                0.000000                 0              6        1000.0   
8947                0.000000                 0              5        1000.0   
8948                0.166667                 2              0         500.0   
8949                0.333333                 2             23        1200.0   

         PAYMENTS  MINIMUM_PAYMENTS  PRC_FULL_PAYMENT  TENURE  Clusters  
0      201.802084        139.509787          0.000000      12         1  
1     4103.032597       1072.340217          0.222222      12         0  
2      622.066742        627.284787          0.000000      12         0  
3        0.000000        312.343947          0.000000      12         1  
4      678.334763        244.791237          0.000000      12         0  
...           ...               ...      

In [3]:
df.drop(columns=['CUST_ID'], inplace=True)
df.isna().sum()

BALANCE                             0
BALANCE_FREQUENCY                   0
PURCHASES                           0
ONEOFF_PURCHASES                    0
INSTALLMENTS_PURCHASES              0
CASH_ADVANCE                        0
PURCHASES_FREQUENCY                 0
ONEOFF_PURCHASES_FREQUENCY          0
PURCHASES_INSTALLMENTS_FREQUENCY    0
CASH_ADVANCE_FREQUENCY              0
CASH_ADVANCE_TRX                    0
PURCHASES_TRX                       0
CREDIT_LIMIT                        0
PAYMENTS                            0
MINIMUM_PAYMENTS                    0
PRC_FULL_PAYMENT                    0
TENURE                              0
Clusters                            0
dtype: int64

In [4]:
x, y = df[[i for i in df.columns if i!='Clusters']], df[['Clusters']]
train_x, test_x, train_y, test_y = train_test_split(x, y, test_size = 0.2, random_state = 0)
columns = train_x.columns
#train_x, test_x, train_y, test_y = train_x.values, test_x.values, train_y.values, test_y.values

hp = [7.37855883e-05, 4.99178207e-05, 1.70000000e+01]
hp = [hp[0], hp[1], np.round(hp[2]).astype(int)]
clf = DTC(min_samples_split=hp[0], min_samples_leaf=hp[1], max_features=hp[2], random_state=1)
clf.fit(train_x, train_y)
clf.score(train_x, train_y), clf.score(test_x, test_y)

(1.0, 0.9832402234636871)

In [5]:
pred = clf.predict(test_x)
confusion_matrix(test_y, pred), accuracy_score(test_y, pred)

(array([[ 731,   15],
        [  15, 1029]]), 0.9832402234636871)

In [19]:
#tree.plot_tree(clf, feature_names=train_x.columns, class_names=['cl0', 'cl1'])
viz = dtreeviz(clf, train_x.values, train_y.values.ravel(), target_name='Cluster',feature_names=list(test_x.columns), 
               class_names=["cl0", "cl1"], orientation='LR'  # need class_names for classifier
              )
viz.view() 

/home/skyolia/anaconda3/envs/tensorflow_gpuenv/lib/python3.6/site-packages/matplotlib/font_manager.py:1328: UserWarning:

findfont: Font family ['Arial'] not found. Falling back to DejaVu Sans



In [99]:
from sklearn.inspection import permutation_importance
from sklearn.metrics import fbeta_score, make_scorer


result = permutation_importance(clf, test_x, test_y, n_repeats=10, random_state=42, n_jobs=2, scoring='f1_weighted')
fig = go.Figure()
# Use x instead of y argument for horizontal plot
for i in range(train_x.shape[1]):
    fig.add_trace(go.Box(x=result['importances'][i], name=columns[i]))

fig.show()

In [149]:
train_x.loc[train_x['Age']=='Old']

Age  Gender OwnHome  Married Location  Salary  Children Catalogs  \
513  Old    Male    Rent   Single    Close   32400         1       12   
810  Old  Female     Own   Single    Close   12700         2        6   
37   Old  Female     Own  Married    Close   41600         0       18   
890  Old  Female     Own  Married    Close   62800         0       18   
813  Old  Female    Rent  Married    Close   71800         0       24   
..   ...     ...     ...      ...      ...     ...       ...      ...   
849  Old  Female     Own   Single    Close   32500         0       24   
804  Old  Female     Own  Married    Close   26700         0       24   
723  Old    Male     Own  Married      Far   74500         0       18   
9    Old    Male     Own  Married      Far   80700         0       18   
707  Old    Male     Own   Single    Close   41900         0        6   

     AmountSpent  
513        515.0  
810         65.0  
37         982.0  
890       1403.0  
813       1946.0  
..           ...  
849        883.0  
804       1120.0  
723       1413.0  
9         3034.0  
707        654.0  

[157 rows x 9 columns]

In [95]:
import json
clf.save_model(
    "multiclass_model.json",
    format="json",
    pool=pool  # is required for model with cat_features to obtain applicable model
)

multilclass_model = json.load(open("multiclass_model.json", "r"))
multilclass_model['oblivious_trees'][0]

{'leaf_values': [-0.18494623931505347,
  0.16800000250339509,
  0,
  0,
  -0.13513513714880557,
  0.1736263762136082,
  -0.13913043685581372,
  0.19444444734189245],
 'leaf_weights': [174, 63, 0, 0, 25, 79, 34, 420],
 'splits': [{'border': 7.999999046325684,
   'ctr_target_border_idx': 0,
   'split_index': 4,
   'split_type': 'OnlineCtr'},
  {'border': 47550,
   'float_feature_index': 0,
   'split_index': 1,
   'split_type': 'FloatFeature'},
  {'border': 35700,
   'float_feature_index': 0,
   'split_index': 0,
   'split_type': 'FloatFeature'}]}

In [15]:
from sklearn.datasets import *
iris = load_iris()
iris.target.shape

(150,)

In [9]:
reduced_df = pd.DataFrame(data=umap, columns=['umap_1', 'umap_2'])
reduced_df.to_csv('/home/skyolia/JupyterProjects/data/credit_card/reduced_data.csv', sep=',', index=False)

In [10]:
umap

array([[-12.699457, -39.52393 ],
       [-10.11495 , -49.32107 ],
       [-16.605284, -44.837387],
       ...,
       [-13.514652, -43.212513],
       [-10.655134, -44.738758],
       [-11.635626, -44.467594]], dtype=float32)